In [2]:
!pip install -U -q pip tensorflow geopandas folium mapclassify google-cloud-storage google-cloud-bigquery[pandas] db-dtypes

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 22.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 475.2/475.2 MB 2.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 65.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100.3/100.3 kB 11.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.1/121.1 kB 13.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 222.8/222.8 kB 23.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.5/5.5 MB 88.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 442.0/442.0 kB 32.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 75.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 183.3/183.3 kB 18.9 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
lida 0.0.10 

In [3]:
import folium
import os
import requests
import zipfile
import geopandas as gpd
from tqdm import tqdm

import os
import zipfile
from google.cloud import storage, bigquery
import geopandas as gpd
import pandas as pd


The shapefiles are available at https://www2.census.gov/geo/tiger/TIGER2019/

In [4]:
from google.colab import userdata
import google.auth
from google.oauth2 import service_account
import json

# Step 1: Retrieve the credentials content and convert it into a dictionary
credentials_content = userdata.get('GOOGLE_APPLICATION_CREDENTIALS')
credentials_dict = json.loads(credentials_content)

# Step 2: Create credentials from the dictionary
credentials = service_account.Credentials.from_service_account_info(credentials_dict, scopes=["https://www.googleapis.com/auth/cloud-platform"])



# US States and US Counties

In [5]:
state_url = 'https://www2.census.gov/geo/tiger/TIGER2019/STATE/tl_2019_us_state.zip'
states_gdf = gpd.GeoDataFrame.from_file(state_url)

In [6]:
counties_url = 'https://www2.census.gov/geo/tiger/TIGER2019/COUNTY/tl_2019_us_county.zip'
counties_gdf = gpd.GeoDataFrame.from_file(counties_url)

In [7]:
states = sorted(states_gdf['STATEFP'].values)

In [17]:
counties = counties_gdf.filter(['STATEFP', 'COUNTYFP']).values

In [18]:
counties = sorted(counties, key=lambda x: (x[0],x[1]))

# Download state, county, tract, water data to Google Bucket


In [ ]:
def download_file_and_upload_to_gcs(url, local_path, bucket_name, destination_blob_name):
    """
    Downloads a file from a URL and uploads it to Google Cloud Storage.

    Args:
    url (str): URL of the file to download.
    local_path (str): Local path to save the file.
    bucket_name (str): Name of the GCS bucket.
    destination_blob_name (str): Destination blob name in the GCS bucket.
    """
    # Download file
    response = requests.get(url)
    with open(local_path, 'wb') as file:
        file.write(response.content)

    # Upload to Google Cloud Storage
    storage_client = storage.Client()
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(destination_blob_name)

    blob.upload_from_filename(local_path)

In [ ]:
# Download states
download_file_and_upload_to_gcs(state_url, 'maps/tl_2019_us_state.zip', 'census_shapefiles', 'states/tl_2019_us_state.zip')

In [ ]:
# Download counties
download_file_and_upload_to_gcs(counties_url, 'maps/tl_2019_us_county.zip', 'census_shapefiles', 'counties/tl_2019_us_county.zip')

In [ ]:
# Download tracts
for STATEFP in tqdm(states):
    filename = f"tl_2019_{STATEFP}_tract.zip"
    tract_url = f"https://www2.census.gov/geo/tiger/TIGER2019/TRACT/{filename}"
    download_file_and_upload_to_gcs(tract_url, f'maps/{filename}', 'census_shapefiles', f'tracts/{filename}')


In [ ]:
# Download blockgroups
for STATEFP in tqdm(states):
    filename = f"tl_2019_{STATEFP}_bg.zip"
    tract_url = f"https://www2.census.gov/geo/tiger/TIGER2019/BG/{filename}"
    download_file_and_upload_to_gcs(tract_url, f'maps/{filename}', 'census_shapefiles', f'blockgroups/{filename}')

In [ ]:
# Download blocks
for STATEFP in tqdm(states):
    filename = f"tl_2019_{STATEFP}_tabblock10.zip"
    tract_url = f"https://www2.census.gov/geo/tiger/TIGER2019/TABBLOCK/{filename}"
    download_file_and_upload_to_gcs(tract_url, f'maps/{filename}', 'census_shapefiles', f'blocks/{filename}')


In [ ]:
# Download water areas
for STATEFP, COUNTYFP in tqdm(counties):
    filename = f"tl_2019_{STATEFP+COUNTYFP}_areawater.zip"
    tract_url = f"https://www2.census.gov/geo/tiger/TIGER2019/AREAWATER/{filename}"
    download_file_and_upload_to_gcs(tract_url, f'maps/{filename}', 'census_shapefiles', f'areawater/{filename}')

# Merge Water Areas to State-based Files

In [19]:
def get_geodf_from_shp(bucket_name, shapefile_blob_name, temp_dir='temp'):
    # Initialize Google Cloud clients
    storage_client = storage.Client(credentials=credentials, project=credentials.project_id)

    # Create the temporary directory if it does not exist
    os.makedirs(temp_dir, exist_ok=True)

    # Download the shapefile ZIP from the bucket
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(shapefile_blob_name)

    # Create the full path for the zip file, ensuring all subdirectories exist
    zip_path = os.path.join(temp_dir, shapefile_blob_name)
    os.makedirs(os.path.dirname(zip_path), exist_ok=True)

    blob.download_to_filename(zip_path)

    # Extract the ZIP file
    with zipfile.ZipFile(zip_path, 'r') as zip_ref:
        zip_ref.extractall(temp_dir)

    # Find the .shp file inside the extracted folder
    shp_path = None
    for root, dirs, files in os.walk(temp_dir):
        for filename in files:
            if filename.endswith('.shp'):
                shp_path = os.path.join(root, filename)
                break
        if shp_path:
            break

    if not shp_path:
        raise FileNotFoundError("No .shp file found in the extracted ZIP.")

    # Read the shapefile into a GeoDataFrame
    gdf = gpd.read_file(shp_path)

    # Convert the geometries to a BigQuery-friendly format (e.g., WKT)
    gdf['geometry'] = gdf['geometry'].apply(lambda x: x.wkt)

    # Convert the GeoDataFrame to a Pandas DataFrame
    df = pd.DataFrame(gdf)

    # Clean up: remove temporary files and directories
    for root, dirs, files in os.walk(temp_dir, topdown=False):
        for name in files:
            os.remove(os.path.join(root, name))
        for name in dirs:
            os.rmdir(os.path.join(root, name))

    return df

def get_geodf_from_geojson(bucket_name, shapefile_blob_name, temp_dir='temp'):
    # Initialize Google Cloud clients
    storage_client = storage.Client(credentials=credentials, project=credentials.project_id)

    # Create the temporary directory if it does not exist
    os.makedirs(temp_dir, exist_ok=True)

    # Download the shapefile ZIP from the bucket
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(shapefile_blob_name)

    # Create the full path for the zip file, ensuring all subdirectories exist
    blob_path = os.path.join(temp_dir, shapefile_blob_name)
    os.makedirs(os.path.dirname(blob_path), exist_ok=True)

    blob.download_to_filename(blob_path)

    # Read the shapefile into a GeoDataFrame
    gdf = gpd.read_file(blob_path)

    # Convert the geometries to a BigQuery-friendly format (e.g., WKT)
    gdf['geometry'] = gdf['geometry'].apply(lambda x: x.wkt)

    # Convert the GeoDataFrame to a Pandas DataFrame
    df = pd.DataFrame(gdf)

    # Clean up: remove temporary files and directories
    for root, dirs, files in os.walk(temp_dir, topdown=False):
        for name in files:
            os.remove(os.path.join(root, name))
        for name in dirs:
            os.rmdir(os.path.join(root, name))

    return df


In [ ]:
def save_geodfs_to_bucket(geodf_list, bucket_name, destination_blob_name, temp_file='temp.geojson'):
    """
    Combines a list of GeoDataFrames and saves them as one GeoDataFrame in a Google Cloud Storage bucket.

    Args:
    geodf_list (list): List of GeoDataFrames.
    bucket_name (str): Name of the Google Cloud Storage bucket.
    destination_blob_name (str): The destination file name in the bucket.
    temp_file (str, optional): Temporary local file name to store combined GeoDataFrame. Defaults to 'temp.geojson'.
    """

    combined_df = pd.concat(geodf_list, ignore_index=True)
    geom = gpd.GeoSeries.from_wkt(combined_df['geometry'])
    combined_df = combined_df.drop('geometry', axis='columns')

    # Combine GeoDataFrames
    combined_geodf = gpd.GeoDataFrame(combined_df, geometry=geom)
    combined_geodf.crs = {'init': 'epsg:4326'}

    # Save combined GeoDataFrame to a file
    combined_geodf.to_file(temp_file, driver='GeoJSON')

    # Initialize Google Cloud Storage client
    storage_client = storage.Client()

    # Upload the file to Google Cloud Storage
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(destination_blob_name)
    blob.upload_from_filename(temp_file)

    # Optionally, clean up the local temporary file
    os.remove(temp_file)

    print(f"Combined GeoDataFrame uploaded to {bucket_name}/{destination_blob_name}")


In [ ]:
# Merge water areas
for STATEFP in tqdm(states):
  state_gdfs = []
  for COUNTYFP in tqdm([c for s,c in counties if s==STATEFP]):
    # if s!=STATEFP: continue
    # print(f"{STATEFP}, {COUNTYFP}")
    filename = f"tl_2019_{STATEFP+COUNTYFP}_areawater.zip"
    gdf = get_geodf_from_shp('census_shapefiles', f'areawater/{filename}')
    gdf['STATEFP'] = STATEFP
    gdf['COUNTYFP'] = COUNTYFP
    state_gdfs.append(gdf)
  save_geodfs_to_bucket(state_gdfs, 'census_shapefiles', f"areawater_states/tl_2019_{STATEFP}_areawater.geojson")

#  Import shapes to Bigquery

In [20]:
def upload_geodf_to_bigquery(df, bigquery_dataset_id, bigquery_table_id):

    bigquery_client = bigquery.Client(credentials=credentials, project=credentials.project_id)

    # Create a BigQuery table and upload the DataFrame
    table_id = f"{bigquery_dataset_id}.{bigquery_table_id}"
    job = bigquery_client.load_table_from_dataframe(df, table_id)
    job.result()  # Wait for the job to complete




In [19]:
def convert_wkt_to_geography(bigquery_dataset_id, bigquery_table_id):

    bigquery_client = bigquery.Client(credentials=credentials, project=credentials.project_id)
    sql = f"""
        CREATE OR REPLACE TABLE `{bigquery_dataset_id}.{bigquery_table_id}` AS
          SELECT *, ST_GeogFromText(geometry) AS geography
          FROM `{bigquery_dataset_id}.{bigquery_table_id}`;
        ALTER TABLE `{bigquery_dataset_id}.{bigquery_table_id}`
        DROP COLUMN geometry;
    """
    query_job = bigquery_client.query(sql)
    query_job.result()  # Wait for the query to complete

In [ ]:
gdf = get_geodf_from_shp('census_shapefiles', 'states/tl_2019_us_state.zip')
upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'us_states')

In [ ]:
gdf = get_geodf_from_shp('census_shapefiles', 'counties/tl_2019_us_county.zip')
upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'us_counties')

In [ ]:
for STATEFP in tqdm(states):
    filename = f"tracts/tl_2019_{STATEFP}_tract.zip"
    gdf = get_geodf_from_shp('census_shapefiles', filename)
    upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'us_tracts')

In [ ]:
for STATEFP in tqdm(states):
    filename = f"blockgroups/tl_2019_{STATEFP}_bg.zip"
    gdf = get_geodf_from_shp('census_shapefiles', filename)
    upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'us_blockgroups')

In [ ]:
for STATEFP in tqdm(states):
    filename = f"blocks/tl_2019_{STATEFP}_tabblock10.zip"
    gdf = get_geodf_from_shp('census_shapefiles', filename)
    upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'us_blocks')

In [ ]:
for STATEFP in tqdm(states):
  filename = f'areawater_states/tl_2019_{STATEFP}_areawater.geojson'
  gdf = get_geodf_from_geojson('census_shapefiles', filename)
  upload_geodf_to_bigquery(gdf, 'nyu-datasets.shapefiles', 'areawater')

In [20]:
convert_wkt_to_geography('nyu-datasets.shapefiles', 'us_blocks')

# Subtract Area Water

In [ ]:
pre_aggregate_query = """
CREATE OR REPLACE TABLE `shapefiles.us_counties_nowater` AS

WITH WaterAgg AS (
  SELECT
    A.STATEFP,
    A.COUNTYFP,
    ST_Union_Agg(A.geography) AS agg_geography
  FROM
    `nyu-datasets.shapefiles.areawater` AS A
  GROUP BY
    A.STATEFP, A.COUNTYFP
)
SELECT
  C.GEOID, C.STATEFP, C.COUNTYFP,
  ST_Difference(C.geography, WA.agg_geography) AS diff_geography
FROM
  `nyu-datasets.shapefiles.us_counties` AS C
LEFT JOIN
  WaterAgg AS WA
ON
  C.STATEFP = WA.STATEFP AND C.COUNTYFP = WA.COUNTYFP

"""

bigquery_client = bigquery.Client(credentials=credentials, project=credentials.project_id)
bigquery_client.query(pre_aggregate_query).result()


In [ ]:
pre_aggregate_query = """
CREATE OR REPLACE TABLE `shapefiles.us_tracts_nowater` AS

WITH WaterAgg AS (
  SELECT
    A.STATEFP,
    A.COUNTYFP,
    ST_Union_Agg(A.geography) AS agg_geography
  FROM
    `nyu-datasets.shapefiles.areawater` AS A
  GROUP BY
    A.STATEFP, A.COUNTYFP
)
SELECT
  C.GEOID, C.STATEFP, C.COUNTYFP, C.TRACTCE,
  ST_Difference(C.geography, WA.agg_geography) AS diff_geography
FROM
  `nyu-datasets.shapefiles.us_tracts` AS C
LEFT JOIN
  WaterAgg AS WA
ON
  C.STATEFP = WA.STATEFP AND C.COUNTYFP = WA.COUNTYFP

"""

bigquery_client = bigquery.Client(credentials=credentials, project=credentials.project_id)
bigquery_client.query(pre_aggregate_query).result()


In [ ]:
pre_aggregate_query = """
CREATE OR REPLACE TABLE `shapefiles.us_blockgroups_nowater` AS

WITH WaterAgg AS (
  SELECT
    A.STATEFP,
    A.COUNTYFP,
    ST_Union_Agg(A.geography) AS agg_geography
  FROM
    `nyu-datasets.shapefiles.areawater` AS A
  GROUP BY
    A.STATEFP, A.COUNTYFP
)
SELECT
  C.GEOID, C.STATEFP, C.COUNTYFP, C.TRACTCE, C.BLKGRPCE,
  ST_Difference(C.geography, WA.agg_geography) AS diff_geography
FROM
  `nyu-datasets.shapefiles.us_blockgroups` AS C
LEFT JOIN
  WaterAgg AS WA
ON
  C.STATEFP = WA.STATEFP AND C.COUNTYFP = WA.COUNTYFP

"""

bigquery_client = bigquery.Client(credentials=credentials, project=credentials.project_id)
bigquery_client.query(pre_aggregate_query).result()


In [ ]:
pre_aggregate_query = """
CREATE OR REPLACE TABLE `shapefiles.us_blocks_nowater` AS

WITH WaterAgg AS (
  SELECT
    A.STATEFP,
    A.COUNTYFP,
    ST_Union_Agg(A.geography) AS agg_geography
  FROM
    `nyu-datasets.shapefiles.areawater` AS A
  GROUP BY
    A.STATEFP, A.COUNTYFP
)
SELECT
  C.GEOID10, C.STATEFP10, C.COUNTYFP10, C.TRACTCE10, C.BLOCKCE10,
  ST_Difference(C.geography, WA.agg_geography) AS diff_geography
FROM
  `nyu-datasets.shapefiles.us_blocks` AS C
LEFT JOIN
  WaterAgg AS WA
ON
  C.STATEFP10 = WA.STATEFP AND C.COUNTYFP10 = WA.COUNTYFP

"""

bigquery_client = bigquery.Client(credentials=credentials, project=credentials.project_id)
bigquery_client.query(pre_aggregate_query).result()


In [21]:
bigquery_client = bigquery.Client(credentials=credentials, project=credentials.project_id)

sql = """
  SELECT
    *
  FROM
    `shapefiles.us_blocks`
  WHERE STATEFP10='36' AND COUNTYFP10='061'
"""

df = bigquery_client.query(sql)

In [22]:
gdf = df.to_geodataframe()

In [24]:
gdf.explore(
    figsize=(20, 20),
    edgecolor="black",
    linewidth=0.1,
    zorder=0,
    color = None
)

In [ ]:
gdf[~gdf['diff_geography'].is_empty]

In [23]:
gdf[~gdf['diff_geography'].is_empty].explore(
    figsize=(20, 20),
    edgecolor="black",
    linewidth=0.1,
    zorder=0,
    color = None
)

KeyError: ignored